In [1]:
using DifferentialEquations
using Plots
using Interact

HTML{String}("<script>\n// Immediately-invoked-function-expression to avoid global variables.\n(function() {\n    var warning_div = document.getElementById(\"webio-warning-5168487717206083864\");\n    var hide = function () {\n        var script = document.getElementById(\"webio-setup-11128147866843276870\");\n        var parent = script && script.parentElement;\n        var grandparent = parent && parent.parentElement;\n        if (grandparent) {\n            grandparent.style.display = \"none\";\n        }\n        warning_div.style.display = \"none\";\n    };\n    if (typeof Jupyter !== \"undefined\") {\n        console.log(\"WebIO detected Jupyter notebook environment.\");\n        // Jupyter notebook.\n        var extensions = (\n            Jupyter\n            && Jupyter.notebook.config.data\n            && Jupyter.notebook.config.data.load_extensions\n        );\n        if (extensions && extensions[\"webio-jupyter-notebook\"]) {\n            // Extension already loaded.\n            console.log(\"Jupyter WebIO nbextension detected; not loading ad-hoc.\");\n            hide();\n            return;\n        }\n    } else if (window.location.pathname.includes(\"/lab\")) {\n        // Guessing JupyterLa\n        console.log(\"Jupyter Lab detected; make sure the @webio/jupyter-lab-provider labextension is installed.\");\n        hide();\n        return;\n    }\n})();\n\n</script>\n<p\n    id=\"webio-warning-5168487717206083864\"\n    class=\"output_text output_stderr\"\n    style=\"padding: 1em; font-weight: bold;\"\n>\n    Unable to load WebIO. Please make sure WebIO works for your Jupyter client.\n    For troubleshooting, please see <a href=\"https://juliagizmos.github.io/WebIO.jl/latest/providers/ijulia/\">\n    the WebIO/IJulia documentation</a>.\n    <!-- TODO: link to installation docs. -->\n</p>\n")

In [109]:
g_na = 120;
g_k = 36;
g_l = 0.3;
e_na = 50;
e_k = -77;
e_l = -54.4;

In [110]:
alpha_m(v) = (2.5 - 0.1 * (v + 65)) / (exp(2.5 - 0.1 * (v + 65)) -1)
beta_m(v) = 4 * exp(-(v + 65) / 18)
alpha_h(v) = 0.07 * exp(- (v + 65) / 20)
beta_h(v) = 1. / (exp(3.0 - 0.1 * (v + 65)) + 1)
alpha_n(v) = (0.1-0.01*(v+65)) / (exp(1-0.1*(v+65)) -1)
beta_n(v) = 0.125 * exp(-(v + 65) / 80)

beta_n (generic function with 1 method)

In [120]:
vs = -100.0:0.01:100.0

-100.0:0.01:100.0

In [130]:
v_inf = [v for v in vs];
m_inf = [alpha_m(v)/(alpha_m(v)+ beta_m(v)) for v in vs];
n_inf = [alpha_n(v)/(alpha_n(v)+ beta_n(v)) for v in vs];
h_inf = [alpha_h(v)/(alpha_h(v)+ beta_h(v)) for v in vs];

t_m = [1/(alpha_m(v)+ beta_m(v)) for v in vs];
t_n = [1/(alpha_n(v)+ beta_n(v)) for v in vs];
t_h = [1/(alpha_h(v)+ beta_h(v)) for v in vs];

In [142]:
p1 = plot(v_inf, m_inf, xlabel = "Membrane Potential, mV", ylabel = "x_∞(V)", label = "m")
plot!(v_inf, n_inf, label = "n")
plot!(v_inf, h_inf, label = "h")

p2 = plot(v_inf, t_m, xlabel = "Membrane Potential, mV", ylabel = "τ_0(V)", label = "m")
plot!(v_inf, t_n, label = "n")
plot!(v_inf, t_h, label = "h")

hbox(p1, p2)


(div { style=Dict("display" => "flex","flex-direction" => "row") }
  Plot{Plots.GRBackend() n=3}
  Plot{Plots.GRBackend() n=3})

In [154]:
function I_t(A, T, p, t)
    if t%T < T-p
        return 0
    else
        return A
    end
end

I_t (generic function with 2 methods)

In [155]:
function huxley_ode!(du, u, p, t)
    
    v, m, h, n = u
    A, T, period = p
    
    I = I_t(A, T, period, t)
    
    dv = -g_na * m^3 * h * (v - e_na) - g_k * n^4 * (v - e_k) - g_l * (v - e_l) + I
    dm = alpha_m(v) * (1 - m) - beta_m(v) * m
    dh = alpha_h(v) * (1 - h) - beta_h(v) * h
    dn = alpha_n(v) * (1 - n) - beta_n(v) * n
    
    du .= (dv, dm, dh, dn)
end

huxley_ode! (generic function with 1 method)

In [156]:
v0 = 1.0
m0 = 0.0
h0 = 0.0
n0 = 0.0

initial_values = [v0, m0, h0, n0];
t_span = [0.0, 100.0];

In [157]:
amplitudes = -5.75:0.5:5.75
T = 15
ps = 3:0.5:9
ts = 0:0.01:1000

@manipulate for pulse_amplitude in amplitudes, pulse_width in ps
    params = [pulse_amplitude, T, pulse_width]
    
    problem = ODEProblem(huxley_ode!, initial_values, t_span, params)
    solution = solve(problem, saveat = 0.1);
    
    
    Is = [I_t(pulse_amplitude, T, pulse_width, t) for t in ts]
    
    p1 = plot(solution[1, :], xlabel = "Time", label = "v(t)", ylimit = (-80, 40))
    plot!(ts, Is)
    p2 = plot(solution[2:4, :]', xlabel = "Time", label = ["m(t)" "h(t)" "n(t)"], ylimit = (-0.01, 1))
    hbox(p1, p2)
end

Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["pulse_amplitude"], Dict{Symbol,Any}(:className => "interact ",:style => Dict{Any,Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol,Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol,Any}(:max => 24,:min => 1,:attributes => Dict{Any,Any}(:type => "range",Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}","orient" => "horizontal"),:step => 1,:className => "slider slider is-fullwidth",:style => Dict{Any,Any}()))], Dict{Symbol,Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol,Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol,Any}(:className => "interact-flex-row-right"))], Dict{Symbol,Any}(:className => "interact-flex-row interact-widget")), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing),"index" => (Observable{Any} with 2 listeners. Value:
12, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "/Users/DanielJackson1/.julia/packages/Knockout/IP1uR/src/../assets/knockout.js"), Asset("js", "knockout_punches", "/Users/DanielJackson1/.julia/packages/Knockout/IP1uR/src/../assets/knockout_punches.js"), Asset("js", nothing, "/Users/DanielJackson1/.julia/packages/InteractBase/sOe2Z/src/../assets/all.js"), Asset("css", nothing, "/Users/DanielJackson1/.julia/packages/InteractBase/sOe2Z/src/../assets/style.css"), Asset("css", nothing, "/Users/DanielJackson1/.julia/packages/Interact/SbgIk/src/../assets/bulma_confined.min.css")], Dict{Any,Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")],"index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(sz_max:32,sz_curr:0), Set{AbstractConnection}(), Base.GenericCondition{Base.AlwaysLockedST}(Base.InvasiveLinkedList{Task}(Task (runnable) @0x000000012f450010, Task (runnable) @0x000000012f450010), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"-5.75\",\"-5.25\",\"-4.75\",\"-4.25\",\"-3.75\",\"-3.25\",\"-2.75\",\"-2.25\",\"-1.75\",\"-1.25\",\"-0.75\",\"-0.25\",\"0.25\",\"0.75\",\"1.25\",\"1.75\",\"2.25\",\"2.75\",\"3.25\",\"3.75\"